In [0]:
storage_account = "taxistorag"
container = "datalaketaxi"

root_path = f"abfss://{container}@{storage_account}.dfs.core.windows.net/taxi_data/"

display(dbutils.fs.ls(root_path))


path name size modificationTime abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data/archive/ archive/ 0 1765132667000 abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data/file_history/ file_history/ 0 1765210851000 abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data/lookup/ lookup/ 0 1765131913000 abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data/yellow_tripdata_2024-08.parquet yellow_tripdata_2024-08.parquet 51067350 1765211337000

In [0]:
%sql
USE CATALOG hive_metastore;



In [0]:
%sql
-- -- 1. Créer la base Bronze stockée dans ADLS
CREATE DATABASE IF NOT EXISTS bronze
LOCATION 'abfss://datalaketaxi@taxistorag.dfs.core.windows.net/bronze/';

-- 2. Recréer une table Bronze à partir de l’ancienne
-- CREATE TABLE IF NOT EXISTS hive_metastore.bronze.trips_data
-- USING DELTA
-- AS
-- SELECT count(*) FROM taxi.bronze_db.trips_data;
-- SELECT count(*) FROM hive_metastore.bronze.trips_data LIMIT 10;

In [0]:
%sql
use hive_metastore.bronze;
select current_database();
drop table if exists trips_data;
create table trips_data
USING DELTA
AS
SELECT * FROM taxi.bronze_db.trips_data;



num_affected_rows num_inserted_rows

In [0]:
%python
files = dbutils.fs.ls(root_path)
display(files)


path name size modificationTime abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data/archive/ archive/ 0 1765132667000 abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data/file_history/ file_history/ 0 1765210851000 abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data/lookup/ lookup/ 0 1765131913000 abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data/yellow_tripdata_2024-08.parquet yellow_tripdata_2024-08.parquet 51067350 1765211337000

In [0]:
%python 
# source_folder="dbfs:/FileStore/tables/taxi_nyc_data/bronze_data/"
# filePath= source_folder + "*.parquet"
# # source_file="dbfs:/FileStore/tables/taxi_nyc_data/bronze_data/yellow_tripdata_2024_01.parquet"
# df =spark.read.parquet(filePath)
# display(df)
from pyspark.sql.functions import current_timestamp, col , substring_index
from pyspark.sql.types import StructType, StructField, StringType, IntegerType, DoubleType, TimestampType,LongType
import datetime

# DEfinir le schéma des données
schema = StructType([
    StructField("VendorID", IntegerType(), True),
    StructField("tpep_pickup_datetime", TimestampType(), True),
    StructField("tpep_dropoff_datetime", TimestampType(), True),
    StructField("passenger_count", LongType(), True),
    StructField("trip_distance", DoubleType(), True),
    StructField("RatecodeID", LongType(), True),
    StructField("store_and_fwd_flag", StringType(), True),
    StructField("PULocationID", IntegerType(), True),
    StructField("DOLocationID", IntegerType(), True),
    StructField("payment_type", LongType(), True),
    StructField("fare_amount", DoubleType(), True),
    StructField("extra", DoubleType(), True),
    StructField("mta_tax", DoubleType(), True),
    StructField("tip_amount", DoubleType(), True),
    StructField("tolls_amount", DoubleType(), True),
    StructField("improvement_surcharge", DoubleType(), True),
    StructField("total_amount", DoubleType(), True),
    StructField("congestion_surcharge", DoubleType(), True),
    StructField("Airport_fee", DoubleType(), True)
])
# Dossier sources 
# source_folder = "dbfs:/FileStore/tables/taxi_nyc_data/bronze_data/"
filePath = root_path 
# Lister les fichier parquet
files = [f for f in dbutils.fs.ls(root_path) if f.name.endswith(".parquet")]
if files :
    df = spark.read.schema(schema).parquet(filePath)
    display(df)
    # Ajouter la colonne ingesttime et le nom du fichier
    df= df.withColumn("ingest_time", current_timestamp())\
            .withColumn("file_name", substring_index(col("_metadata.file_path"), "/", -1))
    #Calcule des nombre de ligne 
    added_rows_count= df.count()
    # verifier si la table existe
    if "trips_data" in [t.name for t in spark.catalog.listTables("bronze")]:
        # Calculer le nombre de lignes dans la table
        old_rows_count = spark.table("bronze.trips_data").count()
    else:    
        old_rows_count=0
    print(f"Nombre de lignes dans la table : {old_rows_count}")
    print(f"Nombre de lignes à ingérer : {added_rows_count}")

    #Sauvegarder les données dans la table
    df.write.format("delta").mode("append").option("mergeSchema", True).saveAsTable("trips_data")
    if spark.table("bronze.trips_data").count() != old_rows_count + added_rows_count:
        raise Exception("Controle de l'insertion des données échoué")
    else:
        print("Insertion des données réussie")
    #Archivage
    archive_folder = root_path + "/archive/" + datetime.datetime.now().strftime("%Y-%m-%d-%H-%M-%S")+ "/"

    files = dbutils.fs.ls(root_path)
    for file in files:
        if file.name.endswith(".parquet"):
            dbutils.fs.mv(file.path, archive_folder+file.name)
    print(f"Fichier archivés dans {archive_folder}")
    # afficher le contenu de dossier archive 
    display(dbutils.fs.ls(archive_folder))
else:
    print("Aucun fichier parquet trouvé dans le dossier source.")
# Lire les données


VendorID tpep_pickup_datetime tpep_dropoff_datetime passenger_count trip_distance RatecodeID store_and_fwd_flag PULocationID DOLocationID payment_type fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge total_amount congestion_surcharge Airport_fee 1 2024-08-01T00:21:00Z 2024-08-01T00:36:13Z 1 7.4 1 N 138 80 1 28.9 7.75 0.5 7.65 0.0 1.0 45.8 0.0 1.75 2 2024-08-01T00:20:01Z 2024-08-01T00:41:47Z 1 9.91 1 N 138 239 1 40.8 6.0 0.5 11.55 6.94 1.0 71.04 2.5 1.75 1 2024-08-01T00:17:52Z 2024-08-01T00:41:45Z 0 13.4 1 N 138 88 1 52.0 10.25 0.5 15.0 0.0 1.0 78.75 2.5 1.75 1 2024-08-01T00:49:08Z 2024-08-01T00:55:56Z 0 3.9 1 N 209 137 3 17.0 3.5 0.5 0.0 0.0 1.0 22.0 2.5 0.0 1 2024-08-01T00:38:52Z 2024-08-01T00:42:34Z 1 0.4 1 N 148 144 2 5.1 3.5 0.5 0.0 0.0 1.0 10.1 2.5 0.0 1 2024-08-01T00:57:59Z 2024-08-01T01:03:14Z 1 0.4 1 N 148 144 1 5.8 3.5 0.5 2.15 0.0 1.0 12.95 2.5 0.0 2 2024-08-01T00:15:46Z 2024-08-01T00:29:45Z 2 3.21 1 N 211 233 1 16.3 1.0 0.5 2.13 0.0 1.0 23.43 2.5 0.0 2 2024-08-01T00:32:17Z 2024-08-01T00:45:53Z 1 3.8 1 N 170 239 1 17.7 1.0 0.5 4.54 0.0 1.0 27.24 2.5 0.0 2 2024-08-01T00:48:16Z 2024-08-01T01:09:23Z 1 5.54 1 N 239 148 1 27.5 1.0 0.5 6.5 0.0 1.0 39.0 2.5 0.0 2 2024-07-31T23:30:15Z 2024-07-31T23:40:24Z 1 1.56 1 N 164 229 1 11.4 1.0 0.5 3.0 0.0 1.0 19.4 2.5 0.0 2 2024-08-01T00:04:56Z 2024-08-01T00:12:11Z 1 1.32 1 N 48 68 1 9.3 1.0 0.5 3.58 0.0 1.0 17.88 2.5 0.0 2 2024-08-01T00:13:30Z 2024-08-01T00:15:39Z 1 0.45 1 N 79 107 1 5.1 1.0 0.5 2.02 0.0 1.0 12.12 2.5 0.0 2 2024-08-01T00:18:32Z 2024-08-01T00:33:19Z 1 2.65 1 N 107 48 1 16.3 1.0 0.5 4.26 0.0 1.0 25.56 2.5 0.0 1 2024-08-01T00:44:42Z 2024-08-01T01:06:28Z 2 11.7 1 N 138 64 2 45.0 7.75 0.5 0.0 0.0 1.0 54.25 0.0 1.75 2 2024-08-01T00:13:15Z 2024-08-01T00:18:57Z 1 1.54 1 N 163 236 1 8.6 1.0 0.5 2.72 0.0 1.0 16.32 2.5 0.0 1 2024-08-01T00:44:03Z 2024-08-01T00:50:01Z 5 0.4 1 N 48 230 2 7.2 3.5 0.5 0.0 0.0 1.0 12.2 2.5 0.0 2 2024-08-01T00:22:52Z 2024-08-01T00:35:17Z 1 2.19 1 N 48 137 1 13.5 1.0 0.5 3.7 0.0 1.0 22.2 2.5 0.0 2 2024-08-01T00:01:40Z 2024-08-01T00:14:31Z 1 2.58 1 N 87 137 1 14.9 1.0 0.5 3.98 0.0 1.0 23.88 2.5 0.0 1 2024-08-01T00:12:07Z 2024-08-01T00:21:43Z 2 1.4 1 N 231 148 1 10.7 3.5 0.5 3.1 0.0 1.0 18.8 2.5 0.0 1 2024-08-01T00:42:20Z 2024-08-01T00:49:14Z 1 1.1 1 N 231 209 1 8.6 3.5 0.5 2.7 0.0 1.0 16.3 2.5 0.0 1 2024-08-01T00:54:17Z 2024-08-01T01:26:01Z 1 9.7 1 N 209 116 1 44.3 3.5 0.5 5.92 0.0 1.0 55.22 2.5 0.0 2 2024-08-01T00:01:00Z 2024-08-01T00:06:22Z 3 0.82 1 N 231 13 1 7.2 1.0 0.5 1.22 0.0 1.0 13.42 2.5 0.0 2 2024-08-01T00:16:50Z 2024-08-01T00:28:51Z 1 3.19 1 N 142 161 1 15.6 1.0 0.5 4.12 0.0 1.0 24.72 2.5 0.0 2 2024-08-01T00:48:26Z 2024-08-01T00:48:40Z 1 0.03 2 N 234 113 2 70.0 0.0 0.5 0.0 0.0 1.0 74.0 2.5 0.0 2 2024-08-01T00:49:30Z 2024-08-01T00:52:27Z 1 0.75 1 N 113 79 1 5.8 1.0 0.5 2.0 0.0 1.0 12.8 2.5 0.0 1 2024-08-01T00:06:12Z 2024-08-01T00:37:03Z 1 2.5 1 N 48 229 1 24.0 3.5 0.5 2.0 0.0 1.0 31.0 2.5 0.0 2 2024-08-01T00:11:24Z 2024-08-01T00:17:18Z 1 0.94 1 N 230 161 1 7.9 1.0 0.5 2.58 0.0 1.0 15.48 2.5 0.0 2 2024-08-01T00:38:22Z 2024-08-01T00:49:02Z 1 1.52 1 N 68 162 1 11.4 1.0 0.5 3.0 0.0 1.0 19.4 2.5 0.0 2 2024-08-01T00:03:18Z 2024-08-01T00:56:46Z 1 17.04 1 N 132 37 1 75.1 1.0 0.5 19.4 0.0 1.0 98.75 0.0 1.75 1 2024-08-01T00:31:21Z 2024-08-01T00:54:24Z 1 15.7 1 N 132 108 2 57.6 2.75 0.5 0.0 0.0 1.0 61.85 0.0 1.75 2 2024-08-01T00:50:36Z 2024-08-01T00:51:06Z 2 0.16 5 N 161 161 1 25.0 0.0 0.5 0.0 0.0 1.0 29.0 2.5 0.0 1 2024-08-01T00:44:31Z 2024-08-01T01:31:20Z 1 11.0 99 N 161 197 1 40.5 0.0 0.5 0.0 6.94 1.0 48.94 0.0 0.0 2 2024-08-01T00:01:46Z 2024-08-01T00:09:05Z 4 1.04 1 N 230 170 2 8.6 1.0 0.5 0.0 0.0 1.0 13.6 2.5 0.0 2 2024-08-01T00:29:41Z 2024-08-01T00:37:54Z 1 1.28 1 N 144 79 1 9.3 1.0 0.5 2.86 0.0 1.0 17.16 2.5 0.0 2 2024-08-01T00:33:35Z 2024-08-01T00:42:53Z 2 1.54 1 N 249 79 1 10.7 1.0 0.5 1.0 0.0 1.0 16.7 2.5 0.0 2 2024-08-01T00:56:17Z 2024-08-01T01:15:45Z 1 9.39 1 N 138 48 2 38.0 6.0 0.5 0.0 6.94 1.0 56.69 2.5 1.75 1 2024-0

Nombre de lignes dans la table : 20332093
Nombre de lignes à ingérer : 2979183
Insertion des données réussie
Fichier archivés dans abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data//archive/2025-12-08-16-38-11/


path name size modificationTime abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data/archive/2025-12-08-16-38-11/yellow_tripdata_2024-08.parquet yellow_tripdata_2024-08.parquet 51067350 1765211892000

In [0]:
%sql
SELECT * FROM bronze.trips_data LIMIT 10;

VendorID tpep_pickup_datetime tpep_dropoff_datetime passenger_count trip_distance RatecodeID store_and_fwd_flag PULocationID DOLocationID payment_type fare_amount extra mta_tax tip_amount tolls_amount improvement_surcharge total_amount congestion_surcharge Airport_fee ingest_time file_name 1 2024-03-01T00:18:51Z 2024-03-01T00:23:45Z 0 1.3 1 N 142 239 1 8.6 3.5 0.5 2.7 0.0 1.0 16.3 2.5 0.0 2025-12-01T23:16:48.570545Z yellow_tripdata_2024_03.parquet 1 2024-03-01T00:26:00Z 2024-03-01T00:29:06Z 0 1.1 1 N 238 24 1 7.2 3.5 0.5 3.0 0.0 1.0 15.2 2.5 0.0 2025-12-01T23:16:48.570545Z yellow_tripdata_2024_03.parquet 2 2024-03-01T00:09:22Z 2024-03-01T00:15:24Z 1 0.86 1 N 263 75 2 7.9 1.0 0.5 0.0 0.0 1.0 10.4 0.0 0.0 2025-12-01T23:16:48.570545Z yellow_tripdata_2024_03.parquet 2 2024-03-01T00:33:45Z 2024-03-01T00:39:34Z 1 0.82 1 N 164 162 1 7.9 1.0 0.5 1.29 0.0 1.0 14.19 2.5 0.0 2025-12-01T23:16:48.570545Z yellow_tripdata_2024_03.parquet 1 2024-03-01T00:05:43Z 2024-03-01T00:26:22Z 0 4.9 1 N 263 7 2 25.4 3.5 0.5 0.0 0.0 1.0 30.4 2.5 0.0 2025-12-01T23:16:48.570545Z yellow_tripdata_2024_03.parquet 2 2024-03-01T00:50:42Z 2024-03-01T01:10:40Z 1 5.04 1 N 238 159 2 25.4 1.0 0.5 0.0 0.0 1.0 27.9 0.0 0.0 2025-12-01T23:16:48.570545Z yellow_tripdata_2024_03.parquet 2 2024-03-01T00:08:23Z 2024-03-01T00:17:53Z 1 2.15 1 N 161 141 1 12.1 1.0 0.5 5.13 0.0 1.0 22.23 2.5 0.0 2025-12-01T23:16:48.570545Z yellow_tripdata_2024_03.parquet 2 2024-03-01T00:24:58Z 2024-03-01T00:30:31Z 1 1.1 1 N 236 237 1 8.6 1.0 0.5 2.04 0.0 1.0 15.64 2.5 0.0 2025-12-01T23:16:48.570545Z yellow_tripdata_2024_03.parquet 2 2024-03-01T00:49:40Z 2024-03-01T01:01:25Z 1 2.78 1 N 161 114 1 14.9 1.0 0.5 2.0 0.0 1.0 21.9 2.5 0.0 2025-12-01T23:16:48.570545Z yellow_tripdata_2024_03.parquet 1 2024-03-01T00:21:43Z 2024-03-01T00:24:44Z 1 0.3 1 N 237 141 2 5.1 3.5 0.5 0.0 0.0 1.0 10.1 2.5 0.0 2025-12-01T23:16:48.570545Z yellow_tripdata_2024_03.parquet

In [0]:
%sql
SELECT count(*) FROM bronze.trips_data;
    

count(1) 23311276

In [0]:
%sql 
SELECT DISTINCT file_name FROM bronze.trips_data ORDER BY file_name ASC ;

file_name yellow_tripdata_2024-08.parquet yellow_tripdata_2024_01.parquet yellow_tripdata_2024_02.parquet yellow_tripdata_2024_03.parquet yellow_tripdata_2024_04.parquet yellow_tripdata_2024_05.parquet yellow_tripdata_2024_06.parquet

In [0]:
%sql
DESCRIBE EXTENDED bronze.trips_data;
    

col_name data_type comment VendorID int null tpep_pickup_datetime timestamp null tpep_dropoff_datetime timestamp null passenger_count bigint null trip_distance double null RatecodeID bigint null store_and_fwd_flag string null PULocationID int null DOLocationID int null payment_type bigint null fare_amount double null extra double null mta_tax double null tip_amount double null tolls_amount double null improvement_surcharge double null total_amount double null congestion_surcharge double null Airport_fee double null ingest_time timestamp null file_name string null # Delta Statistics Columns Column Names DOLocationID, improvement_surcharge, tpep_dropoff_datetime, PULocationID, file_name, trip_distance, Airport_fee, tolls_amount, RatecodeID, VendorID, tip_amount, payment_type, fare_amount, passenger_count, store_and_fwd_flag, extra, ingest_time, congestion_surcharge, total_amount, tpep_pickup_datetime, mta_tax Column Selection Method first-32 # Detailed Table Information Catalog hive_metastore Database bronze Table trips_data Created Time Mon Dec 08 16:38:00 UTC 2025 Last Access UNKNOWN Created By Spark 3.5.2 Type MANAGED Location abfss://datalaketaxi@taxistorag.dfs.core.windows.net/bronze/trips_data Provider delta Owner louiscarlosessekenett.francisco@ynov.com Is_managed_location true Table Properties [delta.enableDeletionVectors=true,delta.feature.appendOnly=supported,delta.feature.deletionVectors=supported,delta.feature.invariants=supported,delta.minReaderVersion=3,delta.minWriterVersion=7]

In [0]:
display(dbutils.fs.ls(root_path))

path name size modificationTime abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data/archive/ archive/ 0 1765132667000 abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data/file_history/ file_history/ 0 1765210851000 abfss://datalaketaxi@taxistorag.dfs.core.windows.net/taxi_data/lookup/ lookup/ 0 1765131913000

In [0]:
%sql
-- DROP TABLE IF EXISTS bronze_db.trips_data;

In [0]:
df_zones =spark.read.option("header", "true").option("inferSchema", "true").csv(root_path+"/lookup/taxi_zone_lookup.csv")
display(df_zones)

LocationID Borough Zone service_zone 1 EWR Newark Airport EWR 2 Queens Jamaica Bay Boro Zone 3 Bronx Allerton/Pelham Gardens Boro Zone 4 Manhattan Alphabet City Yellow Zone 5 Staten Island Arden Heights Boro Zone 6 Staten Island Arrochar/Fort Wadsworth Boro Zone 7 Queens Astoria Boro Zone 8 Queens Astoria Park Boro Zone 9 Queens Auburndale Boro Zone 10 Queens Baisley Park Boro Zone 11 Brooklyn Bath Beach Boro Zone 12 Manhattan Battery Park Yellow Zone 13 Manhattan Battery Park City Yellow Zone 14 Brooklyn Bay Ridge Boro Zone 15 Queens Bay Terrace/Fort Totten Boro Zone 16 Queens Bayside Boro Zone 17 Brooklyn Bedford Boro Zone 18 Bronx Bedford Park Boro Zone 19 Queens Bellerose Boro Zone 20 Bronx Belmont Boro Zone 21 Brooklyn Bensonhurst East Boro Zone 22 Brooklyn Bensonhurst West Boro Zone 23 Staten Island Bloomfield/Emerson Hill Boro Zone 24 Manhattan Bloomingdale Yellow Zone 25 Brooklyn Boerum Hill Boro Zone 26 Brooklyn Borough Park Boro Zone 27 Queens Breezy Point/Fort Tilden/Riis Beach Boro Zone 28 Queens Briarwood/Jamaica Hills Boro Zone 29 Brooklyn Brighton Beach Boro Zone 30 Queens Broad Channel Boro Zone 31 Bronx Bronx Park Boro Zone 32 Bronx Bronxdale Boro Zone 33 Brooklyn Brooklyn Heights Boro Zone 34 Brooklyn Brooklyn Navy Yard Boro Zone 35 Brooklyn Brownsville Boro Zone 36 Brooklyn Bushwick North Boro Zone 37 Brooklyn Bushwick South Boro Zone 38 Queens Cambria Heights Boro Zone 39 Brooklyn Canarsie Boro Zone 40 Brooklyn Carroll Gardens Boro Zone 41 Manhattan Central Harlem Boro Zone 42 Manhattan Central Harlem North Boro Zone 43 Manhattan Central Park Yellow Zone 44 Staten Island Charleston/Tottenville Boro Zone 45 Manhattan Chinatown Yellow Zone 46 Bronx City Island Boro Zone 47 Bronx Claremont/Bathgate Boro Zone 48 Manhattan Clinton East Yellow Zone 49 Brooklyn Clinton Hill Boro Zone 50 Manhattan Clinton West Yellow Zone 51 Bronx Co-Op City Boro Zone 52 Brooklyn Cobble Hill Boro Zone 53 Queens College Point Boro Zone 54 Brooklyn Columbia Street Boro Zone 55 Brooklyn Coney Island Boro Zone 56 Queens Corona Boro Zone 57 Queens Corona Boro Zone 58 Bronx Country Club Boro Zone 59 Bronx Crotona Park Boro Zone 60 Bronx Crotona Park East Boro Zone 61 Brooklyn Crown Heights North Boro Zone 62 Brooklyn Crown Heights South Boro Zone 63 Brooklyn Cypress Hills Boro Zone 64 Queens Douglaston Boro Zone 65 Brooklyn Downtown Brooklyn/MetroTech Boro Zone 66 Brooklyn DUMBO/Vinegar Hill Boro Zone 67 Brooklyn Dyker Heights Boro Zone 68 Manhattan East Chelsea Yellow Zone 69 Bronx East Concourse/Concourse Village Boro Zone 70 Queens East Elmhurst Boro Zone 71 Brooklyn East Flatbush/Farragut Boro Zone 72 Brooklyn East Flatbush/Remsen Village Boro Zone 73 Queens East Flushing Boro Zone 74 Manhattan East Harlem North Boro Zone 75 Manhattan East Harlem South Boro Zone 76 Brooklyn East New York Boro Zone 77 Brooklyn East New York/Pennsylvania Avenue Boro Zone 78 Bronx East Tremont Boro Zone 79 Manhattan East Village Yellow Zone 80 Brooklyn East Williamsburg Boro Zone 81 Bronx Eastchester Boro Zone 82 Queens Elmhurst Boro Zone 83 Queens Elmhurst/Maspeth Boro Zone 84 Staten Island Eltingville/Annadale/Prince's Bay Boro Zone 85 Brooklyn Erasmus Boro Zone 86 Queens Far Rockaway Boro Zone 87 Manhattan Financial District North Yellow Zone 88 Manhattan Financial District South Yellow Zone 89 Brooklyn Flatbush/Ditmas Park Boro Zone 90 Manhattan Flatiron Yellow Zone 91 Brooklyn Flatlands Boro Zone 92 Queens Flushing Boro Zone 93 Queens Flushing Meadows-Corona Park Boro Zone 94 Bronx Fordham South Boro Zone 95 Queens Forest Hills Boro Zone 96 Queens Forest Park/Highland Park Boro Zone 97 Brooklyn Fort Greene Boro Zone 98 Queens Fresh Meadows Boro Zone 99 Staten Island Freshkills Park Boro Zone 100 Manhattan Garment District Yellow Zone 101 Queens Glen Oaks Boro Zone 102 Queens Glendale Boro Zone 103 Manhattan Governor's Island/Ellis Island/Liberty Island Yellow Zone 104 Manhattan Governor's Island/Ellis Island/Liberty Island Yellow Zone 105 Manhattan

In [0]:
spark.catalog.setCurrentDatabase("bronze"); df_zones.write.format("delta").mode("ignore").saveAsTable("taxi_zones")


In [0]:
%sql 
SELECT * FROM bronze.taxi_zones LIMIT 10;


LocationID Borough Zone service_zone 1 EWR Newark Airport EWR 2 Queens Jamaica Bay Boro Zone 3 Bronx Allerton/Pelham Gardens Boro Zone 4 Manhattan Alphabet City Yellow Zone 5 Staten Island Arden Heights Boro Zone 6 Staten Island Arrochar/Fort Wadsworth Boro Zone 7 Queens Astoria Boro Zone 8 Queens Astoria Park Boro Zone 9 Queens Auburndale Boro Zone 10 Queens Baisley Park Boro Zone

In [0]:
%sql
select max(tpep_pickup_datetime) from taxi.bronze_db.trips_data;

max(tpep_pickup_datetime) 2026-06-26T23:53:12Z